In [1]:
!pip install tpot
!pip install mljar-supervised
!pip install pandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 87 kB 3.0 MB/s 
     |████████████████████████████████| 255.9 MB 46 kB/s 
     |████████████████████████████████| 139 kB 46.2 MB/s 
  Created wheel for stopit: filename=stopit-1.1.2-py3-none-any.whl size=11953 sha256=9cf6eaf4ef06312ffabf72c46f5ddd72a7d324f20fcb1d2862b9badf8e0acb84
  Stored in directory: /root/.cache/pip/wheels/e2/d2/79/eaf81edb391e27c87f51b8ef901ecc85a5363dc96b8b8d71e3
Successfully built stopit
  Attempting uninstall: xgboost
    Found existing installation: xgboost 0.90
    Uninstalling xgboost-0.90:
      Successfully uninstalled xgboost-0.90
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 112 kB 5.4 MB/s 
     |████████████████████████████████| 2.0 MB 36.5 MB/s 
     |████████████████████████████████| 76.6 MB 134 kB/s 
     |███████████████

In [2]:
import pandas as pd
import tpot as tp
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML

Import Data

In [3]:
sparcs = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
sparcs

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [4]:
sparcs.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Length of Stay', 'Type of Admission', 'Patient Disposition',
       'Discharge Year', 'CCS Diagnosis Code', 'CCS Diagnosis Description',
       'CCS Procedure Code', 'CCS Procedure Description', 'APR DRG Code',
       'APR DRG Description', 'APR MDC Code', 'APR MDC Description',
       'APR Severity of Illness Code', 'APR Severity of Illness Description',
       'APR Risk of Mortality', 'APR Medical Surgical Description',
       'Payment Typology 1', 'Payment Typology 2', 'Payment Typology 3',
       'Birth Weight', 'Abortion Edit Indicator',
       'Emergency Department Indicator', 'Total Charges', 'Total Costs'],
      dtype='object')

In [5]:
sparcs['Length of Stay'].describe()

count     23583
unique       97
top           2
freq       5378
Name: Length of Stay, dtype: object

In [6]:
sparcs['Total Costs'].describe()

count    2.358300e+04
mean     1.472282e+04
std      2.718098e+04
min      6.700000e-01
25%      4.471700e+03
50%      8.320120e+03
75%      1.590874e+04
max      1.591541e+06
Name: Total Costs, dtype: float64

In [7]:
sparcs['Race'].value_counts()

White                     13433
Other Race                 5442
Black/African American     4467
Multi-racial                241
Name: Race, dtype: int64

Binary Version

In [8]:
sparcs['Length of Stay'] = pd.to_numeric(sparcs['Length of Stay'], errors='coerce')
sparcs['sparcs_los'] = sparcs['Length of Stay'].apply(lambda x: 'long' if x > 3 else 'short')
sparcs.drop('Length of Stay', axis=1, inplace=True)
sparcs['sparcs_los'].value_counts()

short    13008
long     10575
Name: sparcs_los, dtype: int64

In [9]:
X = sparcs.drop(columns=['sparcs_los'])
y = sparcs["sparcs_los"]

In [10]:
X

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2 Payment Typology 3  \
0      Private Health Insurance                       NaN                NaN   
1        Blue Cross/Blue Shield                  Self-Pay           Self-Pay   
2                      Self-Pay                  Self-Pay           Self-Pay   
3                      Medicare                  Medicare           Self-Pay   
4        Blue Cross/Blue Shield       

In [11]:
y

0        short
1        short
2        short
3        short
4         long
         ...  
23578     long
23579    short
23580     long
23581     long
23582     long
Name: sparcs_los, Length: 23583, dtype: object

In [12]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.25)

In [13]:
automl = AutoML(results_path="sparcs_binary_los", mode="Explain")

In [14]:
automl.fit(X_train, y_train)

Linear algorithm was disabled.
AutoML directory: sparcs_binary_los
The task is binary_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 0.687821 trained in 1.2 seconds


2_DecisionTree logloss 0.4556 trained in 24.51 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.262653 trained in 25.15 seconds
4_Default_NeuralNetwork logloss 0.453861 trained in 15.96 seconds
5_Default_RandomForest logloss 0.388899 trained in 25.76 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.262653 trained in 2.12 seconds
AutoML fit time: 109.56 seconds
AutoML best model: 3_Default_Xgboost


AutoML(results_path='sparcs_binary_los')

In [15]:
pred = automl.predict(X_test)
pred

array(['short', 'long', 'short', ..., 'long', 'short', 'short'],
      dtype=object)

In [16]:
automl.report()

Testing new data

In [17]:
automl_sparcs_los = AutoML(results_path="sparcs_binary_los")

In [18]:
X_withlos = sparcs.sample(5)
X_withoutlos = X_withlos.drop(columns=['sparcs_los'])

In [19]:
predict = automl.predict(X_withoutlos)
predict

array(['long', 'long', 'long', 'short', 'long'], dtype=object)

In [20]:
values_actual = X_withlos['sparcs_los'].values.tolist()
values_predicted = predict.tolist()
output = pd.DataFrame({'actual': values_actual, 'predicted': values_predicted})
output

actual predicted
0   long      long
1   long      long
2   long      long
3  short     short
4   long      long

Binary Classifier Example

In [21]:
sparcs['Total Costs'].describe()

count    2.358300e+04
mean     1.472282e+04
std      2.718098e+04
min      6.700000e-01
25%      4.471700e+03
50%      8.320120e+03
75%      1.590874e+04
max      1.591541e+06
Name: Total Costs, dtype: float64

In [22]:
sparcs['Total Costs'].value_counts()

884.38      17
2279.63     12
2279.25     11
975.86       9
2102.45      8
            ..
15776.66     1
1428.85      1
5024.84      1
790.61       1
6212.95      1
Name: Total Costs, Length: 23176, dtype: int64

In [24]:
TP = sparcs.drop(columns=['Total Costs'])

In [25]:
TP

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2 Payment Typology 3  \
0      Private Health Insurance                       NaN                NaN   
1        Blue Cross/Blue Shield                  Self-Pay           Self-Pay   
2                      Self-Pay                  Self-Pay           Self-Pay   
3                      Medicare                  Medicare           Self-Pay   
4        Blue Cross/Blue Shield       

In [27]:
EP = sparcs['Total Costs']

In [28]:
EP

0         4747.83
1         2985.64
2         2129.67
3         8454.41
4        34565.03
           ...   
23578     8961.40
23579     2214.06
23580    11083.24
23581     7951.26
23582     6212.95
Name: Total Costs, Length: 23583, dtype: float64

In [29]:
automl2 = AutoML(results_path="SPARCS_Total_Costs", mode="Explain")

In [30]:
automl2.fit(TP, EP)

Linear algorithm was disabled.
AutoML directory: SPARCS_Total_Costs
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline rmse 23541.268908 trained in 1.16 seconds
2_DecisionTree rmse 10272.122412 trained in 13.23 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost rmse 6788.416624 trained in 151.46 seconds
4_Default_NeuralNetwork rmse 20000.046829 trained in 5.89 seconds
5_Default_RandomForest rmse 10616.609688 trained in 22.37 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 6283.46816 trained in 0.36 seconds
AutoML fit time: 204.67 seconds
AutoML best model: Ensemble


AutoML(results_path='SPARCS_Total_Costs')

In [35]:
sparcs["predictions"] = automl2.predict(TP)

In [39]:
print('predictions')
print(sparcs[['Total Costs', 'predictions']])

predictions
       Total Costs   predictions
0          4747.83   5093.876994
1          2985.64   3806.729533
2          2129.67   3161.863810
3          8454.41   7869.876749
4         34565.03  25236.524482
...            ...           ...
23578      8961.40  11314.646553
23579      2214.06   3343.683878
23580     11083.24  12429.880928
23581      7951.26  10580.669013
23582      6212.95   5974.721964

[23583 rows x 2 columns]


Download

In [41]:
!zip -r /content/download.zip /content/

  adding: content/ (stored 0%)
  adding: content/.config/ (stored 0%)
  adding: content/.config/.last_opt_in_prompt.yaml (stored 0%)
  adding: content/.config/.last_update_check.json (deflated 24%)
  adding: content/.config/config_sentinel (stored 0%)
  adding: content/.config/active_config (stored 0%)
  adding: content/.config/configurations/ (stored 0%)
  adding: content/.config/configurations/config_default (deflated 15%)
  adding: content/.config/logs/ (stored 0%)
  adding: content/.config/logs/2022.11.22/ (stored 0%)
  adding: content/.config/logs/2022.11.22/00.13.55.296951.log (deflated 55%)
  adding: content/.config/logs/2022.11.22/00.13.56.045946.log (deflated 53%)
  adding: content/.config/logs/2022.11.22/00.13.23.276767.log (deflated 86%)
  adding: content/.config/logs/2022.11.22/00.13.01.107222.log (deflated 54%)
  adding: content/.config/logs/2022.11.22/00.12.36.088191.log (deflated 92%)
  adding: content/.config/logs/2022.11.22/00.13.32.115099.log (deflated 54%)
  adding: 

In [42]:
from google.colab import files
files.download('/content/download.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>